In [2]:
import os
import json
from pathlib import Path

# List all files in the 'data' directory
data_dir = Path('data')
json_files = sorted(data_dir.glob('*.json'), key=lambda x: int(x.stem))

# Read and store the contents of each JSON file
data = []
for file in json_files:
    with open(file, 'r') as f:
        data.append(json.load(f))

print(f"Loaded {len(data)} JSON files from the 'data' directory.")


Loaded 210 JSON files from the 'data' directory.


In [6]:
data[80].keys()

dict_keys(['services', 'others', 'scoreboard'])

In [12]:
data[80]['scoreboard'][1]["ad"]

{'score': 59261.849062006004, 'weightedScore': 59261.84906200601}

In [3]:
import pandas as pd
import plotly.express as px

# Create dictionaries to store data for each team
team_data = {}

# Get unique service shortnames
service_shortnames = set()
for round_data in data:
    for service in round_data['services']:
        service_shortnames.add(service['shortname'])

# Iterate through each round of data
for round_index, round_data in enumerate(data):
    for team in round_data['scoreboard']:
        shortname = team['shortname']
        
        if shortname not in team_data:
            team_data[shortname] = {
                'score': [],
                'services': {service: {'score': [], 'stolen': [], 'lost': []} for service in service_shortnames}
            }
        
        team_data[shortname]['score'].append(team['score'])
        
        # Collect service scores, stolen, and lost
        for service in team['services']:
            team_data[shortname]['services'][service['shortname']]['score'].append(service['score'])
            team_data[shortname]['services'][service['shortname']]['stolen'].append(service['stolen'])
            team_data[shortname]['services'][service['shortname']]['lost'].append(service['lost'])

# Create DataFrames
df_score = pd.DataFrame({team: data['score'] for team, data in team_data.items()})

# Create service DataFrames
df_services = {service: {
    'score': pd.DataFrame({team: data['services'][service]['score'] for team, data in team_data.items()}),
    'stolen': pd.DataFrame({team: data['services'][service]['stolen'] for team, data in team_data.items()}),
    'lost': pd.DataFrame({team: data['services'][service]['lost'] for team, data in team_data.items()})
} for service in service_shortnames}

# Sort the columns (team shortnames) alphabetically
df_score = df_score.sort_index(axis=1)
for service in df_services:
    for metric in df_services[service]:
        df_services[service][metric] = df_services[service][metric].sort_index(axis=1)

# Create line plots
fig_score = px.line(df_score, labels={'index': 'Round', 'value': 'Score', 'variable': 'Team'},
                    title='Team Scores over Rounds')
fig_score.update_layout(legend_title_text='Teams')

fig_score.show()

# Create service score, stolen, and lost plots
fig_services = {service: {
    'score': px.line(df_services[service]['score'], 
                     labels={'index': 'Round', 'value': f'{service} Score', 'variable': 'Team'},
                     title=f'{service} Scores over Rounds'),
    'stolen': px.line(df_services[service]['stolen'], 
                      labels={'index': 'Round', 'value': f'{service} Stolen', 'variable': 'Team'},
                      title=f'{service} Stolen over Rounds'),
    'lost': px.line(df_services[service]['lost'], 
                    labels={'index': 'Round', 'value': f'{service} Lost', 'variable': 'Team'},
                    title=f'{service} Lost over Rounds')
} for service in service_shortnames}

# Update layouts for better readability
for service in fig_services:
    for fig in fig_services[service].values():
        fig.update_layout(legend_title_text='Teams')

# Show the plots

for service in fig_services:
    for fig in fig_services[service].values():
        fig.show()
    break




In [41]:
df_score

albania     australia       austria       belgium      bulgaria  \
0    40000.000000   5000.000000  40000.000000  40000.000000  40000.000000   
1    39983.229490   2500.000000  39983.229490  39983.229490  39983.229490   
2    39967.837224   1666.666667  39967.837224  39967.837224  39967.837224   
3    39953.634787   8733.899008  39953.634787  39953.634787  39953.634787   
4    38940.472132   7987.119206  39940.472132  39940.472132  39940.472132   
..            ...           ...           ...           ...           ...   
205   7964.623578  29345.522843  71278.707791  23116.416073  30806.050457   
206   7964.623578  29345.522843  71278.707791  23116.416073  30806.050457   
207   7964.623578  29345.522843  71278.707791  23116.416073  30806.050457   
208   7964.623578  29345.522843  71278.707791  23116.416073  30806.050457   
209   7964.623578  29345.522843  71278.707791  23116.416073  30806.050457   

           canada    costa-rica       croatia  cybersecnatlab        cyprus  \
0    35000.000000  35000.000000  30000.000000    40000.000000  40000.000000   
1    35000.000000  37491.614745  29983.229490    40000.000000  39983.229490   
2    35000.000000  36655.945741  29967.837224    40000.000000  39967.837224   
3    35000.000000  36241.959306  31203.634787    40000.000000  39953.634787   
4    35000.000000  35988.088029  31940.472132    40000.000000  39940.472132   
..            ...           ...           ...             ...           ...   
205  48040.177314  19692.574812  23647.793984    39657.534247  27812.959452   
206  48040.177314  19692.574812  23647.793984    39657.534247  27812.959452   
207  48040.177314  19692.574812  23647.793984    39657.534247  27812.959452   
208  48040.177314  19692.574812  23647.793984    39657.534247  27812.959452   
209  48040.177314  19692.574812  23647.793984    39657.534247  27812.959452   

     ...      portugal       romania        serbia     singapore  \
0    ...  40000.000000  35000.000000  35000.000000  40000.000000   
1    ...  39882.606431  34983.229490  32491.614745  37483.229490   
2    ...  39718.141058  34967.837224  33311.891483  38301.170557   
3    ...  39607.349899  34953.634787  32465.226090  38703.634787   
4    ...  39483.440705  34953.634787  27972.180872  38940.472132   
..   ...           ...           ...           ...           ...   
205  ...  26934.998176  63514.095453  28321.240634  17759.538679   
206  ...  26934.998176  63514.095453  28321.240634  17759.538679   
207  ...  26934.998176  63514.095453  28321.240634  17759.538679   
208  ...  26934.998176  63514.095453  28321.240634  17759.538679   
209  ...  26934.998176  63514.095453  28321.240634  17759.538679   

         slovakia      slovenia         spain        sweden   switzerland  \
0    40000.000000  40000.000000  40000.000000  30000.000000  40000.000000   
1    34983.229490  40000.000000  39983.229490  27483.229490  35000.000000   
2    33301.170557  40001.101063  39967.837224  26634.503891  35001.101063   
3    29953.634787  40053.190805  39953.634787  27453.634787  35002.996762   
4    31940.472132  40071.919313  39940.472132  27940.472132  35021.959046   
..            ...           ...           ...           ...           ...   
205  31592.953116  42572.425847  21534.657065  47887.419609  64696.039595   
206  31592.953116  42572.425847  21534.657065  47887.419609  64696.039595   
207  31592.953116  42572.425847  21534.657065  47887.419609  64696.039595   
208  31592.953116  42572.425847  21534.657065  47887.419609  64696.039595   
209  31592.953116  42572.425847  21534.657065  47887.419609  64696.039595   

              usa  
0    40000.000000  
1    39983.229490  
2    39967.837224  
3    39953.634787  
4    38940.472132  
..            ...  
205  46572.626670  
206  46572.626670  
207  46572.626670  
208  46572.626670  
209  46572.626670  

[210 rows x 38 columns]

In [53]:
from IPython.display import HTML
import json

# Convert DataFrame to a format suitable for JavaScript
data = df_score.to_dict(orient='index')
data_json = json.dumps(data)

#save to json
with open('data.json', 'w') as f:
    json.dump(data, f)

# P5.js sketch
p5_sketch = f"""
<!DOCTYPE html>
<html>
<head>
  <title>P5.js Sketch</title>
  <script src="https://cdnjs.cloudflare.com/ajax/libs/p5.js/1.4.0/p5.js"></script>
</head>
<body>
  <div id="p5-sketch"></div>
  <script>
    let data = {data_json};
    let teams = Object.keys(data[0]);
    let rounds = Object.keys(data);
    let positions = [];
    let maxScore = 0;

    function setup() {{
      let canvas = createCanvas(800, 800);
      canvas.parent('p5-sketch');
      
      let hexRadius = width / 12;
      let currentRing = 1;
      let teamCount = 0;
      while (teamCount < teams.length) {{
        for (let i = 0; i < 6; i++) {{
          for (let j = 0; j < currentRing; j++) {{
            let angle = TWO_PI / 6 * i;
            let x = width/2 + cos(angle) * hexRadius * (currentRing - 0.5);
            let y = height/2 + sin(angle) * hexRadius * (currentRing - 0.5);
            positions.push({{x, y}});
            teamCount++;
            if (teamCount === teams.length) break;
          }}
          if (teamCount === teams.length) break;
        }}
        currentRing++;
      }}
      
      for (let round in data) {{
        for (let team in data[round]) {{
          maxScore = max(maxScore, data[round][team]);
        }}
      }}
      
      frameRate(2);  // Slow down the animation
    }}

    function draw() {{
      background(240);
      
      let roundIndex = frameCount % rounds.length;
      let currentRound = rounds[roundIndex];
      
      for (let i = 0; i < teams.length; i++) {{
        let team = teams[i];
        let pos = positions[i];
        let score = data[currentRound][team];
        let size = map(score, 0, maxScore, 5, 50);
        
        fill(100, 100, 255, 200);
        noStroke();
        ellipse(pos.x, pos.y, size, size);
        
        fill(0);
        textAlign(CENTER, CENTER);
        textSize(10);
        text(team, pos.x, pos.y + 30);
        text(int(score), pos.x, pos.y);
      }}
      
      fill(0);
      textAlign(LEFT, TOP);
      textSize(24);
      text(`Round: ${{parseInt(currentRound) + 1}}`, 10, 10);
    }}
  </script>
</body>
</html>
"""

#save to html
with open('p5_sketch.html', 'w') as f:
    f.write(p5_sketch)




In [26]:
import pandas as pd
import numpy as np

# Assuming df_services['Diese-1'] is a DataFrame with 'stolen' and 'lost' columns
mm = df_services['Diese-1']

stolen_data = mm['stolen'].to_dict(orient='index')
lost_data = mm['lost'].to_dict(orient='index')

# Get the list of countries from the first round (assuming all rounds have the same set of countries)
countries = list(stolen_data[0].keys())

# Create dictionaries to store who stole from whom and who lost to whom
round_interactions = {}

for round_num, (stolen_round, lost_round) in enumerate(zip(stolen_data.values(), lost_data.values())):
    stole_from = []
    lost_to = []

    # Track who stole from whom
    for attacker in countries:
        if stolen_round[attacker] > 0:
            for victim in countries:
                if lost_round[victim] > 0:
                    stole_from.append(f"{attacker}:{victim}")  # Attacker stole from victim

    # Track who lost to whom
    for victim in countries:
        if lost_round[victim] > 0:
            for attacker in countries:
                if stolen_round[attacker] > 0:
                    lost_to.append(f"{victim}:{attacker}")  # Victim lost to attacker

    # Store interactions for this round
    round_interactions[round_num] = {
        'stole_from': stole_from,
        'lost_to': lost_to
    }

# Save results as a JSON file
import json
with open('round_interactions.json', 'w') as f:
    json.dump(round_interactions, f, indent=4)

# Print results for verification
for round_num, interactions in round_interactions.items():
    print(f"Round {round_num}:")
    print("Stole from:", interactions['stole_from'])
    print("Lost to:", interactions['lost_to'])
    print("\n")

Round 0:
Stole from: []
Lost to: []


Round 1:
Stole from: ['finland:portugal', 'france:portugal', 'italy:portugal', 'poland:portugal', 'slovenia:portugal', 'switzerland:portugal']
Lost to: ['portugal:finland', 'portugal:france', 'portugal:italy', 'portugal:poland', 'portugal:slovenia', 'portugal:switzerland']


Round 2:
Stole from: ['finland:portugal', 'france:portugal', 'ireland:portugal', 'italy:portugal', 'netherlands:portugal', 'poland:portugal', 'slovenia:portugal', 'switzerland:portugal']
Lost to: ['portugal:finland', 'portugal:france', 'portugal:ireland', 'portugal:italy', 'portugal:netherlands', 'portugal:poland', 'portugal:slovenia', 'portugal:switzerland']


Round 3:
Stole from: ['finland:croatia', 'finland:portugal', 'france:croatia', 'france:portugal', 'ireland:croatia', 'ireland:portugal', 'italy:croatia', 'italy:portugal', 'netherlands:croatia', 'netherlands:portugal', 'poland:croatia', 'poland:portugal', 'slovenia:croatia', 'slovenia:portugal', 'switzerland:croatia', 's

In [5]:
import pandas as pd
import numpy as np
import json

# Create a dictionary to store interactions for all services
all_service_interactions = {}

for service_name, service_data in df_services.items():
    stolen_data = service_data['stolen'].to_dict(orient='index')
    lost_data = service_data['lost'].to_dict(orient='index')

    # Get the list of countries from the first round
    countries = list(stolen_data[0].keys())

    # Create dictionaries to store who stole from whom and who lost to whom
    round_interactions = {}

    for round_num, (stolen_round, lost_round) in enumerate(zip(stolen_data.values(), lost_data.values())):
        stole_from = []
        lost_to = []

        # Track who stole from whom
        for attacker in countries:
            if stolen_round[attacker] > 0:
                for victim in countries:
                    if lost_round[victim] > 0:
                        stole_from.append(f"{attacker}:{victim}")  # Attacker stole from victim

        # Track who lost to whom
        for victim in countries:
            if lost_round[victim] > 0:
                for attacker in countries:
                    if stolen_round[attacker] > 0:
                        lost_to.append(f"{victim}:{attacker}")  # Victim lost to attacker

        # Store interactions for this round (use string keys for consistency)
        round_interactions[str(round_num)] = {
            'stole_from': stole_from,
            'lost_to': lost_to
        }

    # Store interactions for this service
    all_service_interactions[service_name] = round_interactions

# Save results as a JSON file
with open('all_service_interactions.json', 'w') as f:
    json.dump(all_service_interactions, f, indent=4)

# Print results for verification (limited to first 5 rounds of each service)
for service_name, interactions in all_service_interactions.items():
    print(f"Service: {service_name}")
    for round_num in range(min(5, len(interactions))):
        print(f"  Round {round_num}:")
        print("    Stole from:", interactions[str(round_num)]['stole_from'])
        print("    Lost to:", interactions[str(round_num)]['lost_to'])
    print("\n")

Service: Sanromolo
  Round 0:
    Stole from: []
    Lost to: []
  Round 1:
    Stole from: []
    Lost to: []
  Round 2:
    Stole from: []
    Lost to: []
  Round 3:
    Stole from: []
    Lost to: []
  Round 4:
    Stole from: []
    Lost to: []


Service: CookingNonna
  Round 0:
    Stole from: []
    Lost to: []
  Round 1:
    Stole from: []
    Lost to: []
  Round 2:
    Stole from: []
    Lost to: []
  Round 3:
    Stole from: []
    Lost to: []
  Round 4:
    Stole from: []
    Lost to: []


Service: APT-Finals-1
  Round 0:
    Stole from: []
    Lost to: []
  Round 1:
    Stole from: []
    Lost to: []
  Round 2:
    Stole from: []
    Lost to: []
  Round 3:
    Stole from: []
    Lost to: []
  Round 4:
    Stole from: []
    Lost to: []


Service: Diese-2
  Round 0:
    Stole from: []
    Lost to: []
  Round 1:
    Stole from: []
    Lost to: []
  Round 2:
    Stole from: []
    Lost to: []
  Round 3:
    Stole from: []
    Lost to: []
  Round 4:
    Stole from: []
    Lost t

In [19]:
stolen_data

{0: {'albania': 0,
  'australia': 0,
  'austria': 0,
  'belgium': 0,
  'bulgaria': 0,
  'canada': 0,
  'costa-rica': 0,
  'croatia': 0,
  'cybersecnatlab': 0,
  'cyprus': 0,
  'czech': 0,
  'denmark': 0,
  'estonia': 0,
  'finland': 0,
  'france': 0,
  'germany': 0,
  'greece': 0,
  'hungary': 0,
  'iceland': 0,
  'ireland': 0,
  'italy': 0,
  'kosovo': 0,
  'latvia': 0,
  'liechtenstein': 0,
  'luxembourg': 0,
  'netherlands': 0,
  'norway': 0,
  'poland': 0,
  'portugal': 0,
  'romania': 0,
  'serbia': 0,
  'singapore': 0,
  'slovakia': 0,
  'slovenia': 0,
  'spain': 0,
  'sweden': 0,
  'switzerland': 0,
  'usa': 0},
 1: {'albania': 0,
  'australia': 0,
  'austria': 0,
  'belgium': 0,
  'bulgaria': 0,
  'canada': 0,
  'costa-rica': 0,
  'croatia': 0,
  'cybersecnatlab': 0,
  'cyprus': 0,
  'czech': 0,
  'denmark': 0,
  'estonia': 0,
  'finland': 1,
  'france': 1,
  'germany': 0,
  'greece': 0,
  'hungary': 0,
  'iceland': 0,
  'ireland': 0,
  'italy': 1,
  'kosovo': 0,
  'latvia': 0,

In [16]:
df_services.keys()

dict_keys(['CookingNonna', 'APT-Finals-2', 'fonograph', 'Sanromolo', 'duogesto', 'Diese-2', 'APT-Finals-1', 'Diese-1'])

In [15]:
mm

{'score':          albania    australia       austria      belgium     bulgaria  \
 0    5000.000000   5000.00000   5000.000000  5000.000000  5000.000000   
 1    5000.000000   5000.00000   5000.000000  5000.000000  5000.000000   
 2    5000.000000   5000.00000   5000.000000  5000.000000  5000.000000   
 3    5000.000000   5000.00000   5000.000000  5000.000000  5000.000000   
 4    5000.000000   5000.00000   5000.000000  5000.000000  5000.000000   
 ..           ...          ...           ...          ...          ...   
 205  4916.737467  10491.02707  12469.280374  1263.143558  8818.072115   
 206  4916.737467  10491.02707  12469.280374  1263.143558  8818.072115   
 207  4916.737467  10491.02707  12469.280374  1263.143558  8818.072115   
 208  4916.737467  10491.02707  12469.280374  1263.143558  8818.072115   
 209  4916.737467  10491.02707  12469.280374  1263.143558  8818.072115   
 
           canada  costa-rica      croatia  cybersecnatlab       cyprus  ...  \
 0    5000.000000  50

In [57]:
df_services

{'Diese-1': {'score':          albania    australia       austria      belgium     bulgaria  \
  0    5000.000000   5000.00000   5000.000000  5000.000000  5000.000000   
  1    5000.000000   5000.00000   5000.000000  5000.000000  5000.000000   
  2    5000.000000   5000.00000   5000.000000  5000.000000  5000.000000   
  3    5000.000000   5000.00000   5000.000000  5000.000000  5000.000000   
  4    5000.000000   5000.00000   5000.000000  5000.000000  5000.000000   
  ..           ...          ...           ...          ...          ...   
  205  4916.737467  10491.02707  12469.280374  1263.143558  8818.072115   
  206  4916.737467  10491.02707  12469.280374  1263.143558  8818.072115   
  207  4916.737467  10491.02707  12469.280374  1263.143558  8818.072115   
  208  4916.737467  10491.02707  12469.280374  1263.143558  8818.072115   
  209  4916.737467  10491.02707  12469.280374  1263.143558  8818.072115   
  
            canada  costa-rica      croatia  cybersecnatlab       cyprus  ...

In [61]:
#find out who was attacking who based on the services and lost and stolen
attack_data = {}

for round_data in data:
    for service in round_data['services']:
        if 'attackers' in service and 'victims' in service:
            service_name = service['name']
            if service_name not in attack_data:
                attack_data[service_name] = {'attackers': set(), 'victims': set()}
            
            print(service)


TypeError: 'int' object is not subscriptable

In [62]:
round_data

0

In [31]:
df_score

albania     australia       austria       belgium      bulgaria  \
0    40000.000000   5000.000000  40000.000000  40000.000000  40000.000000   
1    39983.229490   2500.000000  39983.229490  39983.229490  39983.229490   
2    39967.837224   1666.666667  39967.837224  39967.837224  39967.837224   
3    39953.634787   8733.899008  39953.634787  39953.634787  39953.634787   
4    38940.472132   7987.119206  39940.472132  39940.472132  39940.472132   
..            ...           ...           ...           ...           ...   
205   7964.623578  29345.522843  71278.707791  23116.416073  30806.050457   
206   7964.623578  29345.522843  71278.707791  23116.416073  30806.050457   
207   7964.623578  29345.522843  71278.707791  23116.416073  30806.050457   
208   7964.623578  29345.522843  71278.707791  23116.416073  30806.050457   
209   7964.623578  29345.522843  71278.707791  23116.416073  30806.050457   

           canada    costa-rica       croatia  cybersecnatlab        cyprus  \
0    35000.000000  35000.000000  30000.000000    40000.000000  40000.000000   
1    35000.000000  37491.614745  29983.229490    40000.000000  39983.229490   
2    35000.000000  36655.945741  29967.837224    40000.000000  39967.837224   
3    35000.000000  36241.959306  31203.634787    40000.000000  39953.634787   
4    35000.000000  35988.088029  31940.472132    40000.000000  39940.472132   
..            ...           ...           ...             ...           ...   
205  48040.177314  19692.574812  23647.793984    39657.534247  27812.959452   
206  48040.177314  19692.574812  23647.793984    39657.534247  27812.959452   
207  48040.177314  19692.574812  23647.793984    39657.534247  27812.959452   
208  48040.177314  19692.574812  23647.793984    39657.534247  27812.959452   
209  48040.177314  19692.574812  23647.793984    39657.534247  27812.959452   

     ...      portugal       romania        serbia     singapore  \
0    ...  40000.000000  35000.000000  35000.000000  40000.000000   
1    ...  39882.606431  34983.229490  32491.614745  37483.229490   
2    ...  39718.141058  34967.837224  33311.891483  38301.170557   
3    ...  39607.349899  34953.634787  32465.226090  38703.634787   
4    ...  39483.440705  34953.634787  27972.180872  38940.472132   
..   ...           ...           ...           ...           ...   
205  ...  26934.998176  63514.095453  28321.240634  17759.538679   
206  ...  26934.998176  63514.095453  28321.240634  17759.538679   
207  ...  26934.998176  63514.095453  28321.240634  17759.538679   
208  ...  26934.998176  63514.095453  28321.240634  17759.538679   
209  ...  26934.998176  63514.095453  28321.240634  17759.538679   

         slovakia      slovenia         spain        sweden   switzerland  \
0    40000.000000  40000.000000  40000.000000  30000.000000  40000.000000   
1    34983.229490  40000.000000  39983.229490  27483.229490  35000.000000   
2    33301.170557  40001.101063  39967.837224  26634.503891  35001.101063   
3    29953.634787  40053.190805  39953.634787  27453.634787  35002.996762   
4    31940.472132  40071.919313  39940.472132  27940.472132  35021.959046   
..            ...           ...           ...           ...           ...   
205  31592.953116  42572.425847  21534.657065  47887.419609  64696.039595   
206  31592.953116  42572.425847  21534.657065  47887.419609  64696.039595   
207  31592.953116  42572.425847  21534.657065  47887.419609  64696.039595   
208  31592.953116  42572.425847  21534.657065  47887.419609  64696.039595   
209  31592.953116  42572.425847  21534.657065  47887.419609  64696.039595   

              usa  
0    40000.000000  
1    39983.229490  
2    39967.837224  
3    39953.634787  
4    38940.472132  
..            ...  
205  46572.626670  
206  46572.626670  
207  46572.626670  
208  46572.626670  
209  46572.626670  

[210 rows x 38 columns]